# 코로나 분석 프로젝트

Johns Hopkins University 에서 제공하는 코로나 데이터들을 받아온다.

In [2]:
import os 
import requests
for filename in ['time_series_covid19_confirmed_global.csv',
                 'time_series_covid19_deaths_global.csv',
                 'time_series_covid19_recovered_global.csv',
                 'time_series_covid19_confirmed_US.csv',
                 'time_series_covid19_deaths_US.csv']: 
    print(f'Downloading {filename}') 
    url = f'https://raw.githubusercontent.com/CSSEGISandData/COVID-19/master/csse_covid_19_data/csse_covid_19_time_series/{filename}' 
    myfile = requests.get(url) 
    open(filename, 'wb').write(myfile.content)



컬럼명을 1/22/20 -> 2020-01-20 이런 날짜형식으로 쉽게 변경을 한다.

In [3]:
from datetime import datetime 
import pandas as pd 
def _convert_date_str(df): 
    try: 
        df.columns = list(df.columns[:4]) + [datetime.strptime(d, "%m/%d/%y").date().strftime("%Y-%m-%d") for d in df.columns[4:]] 
    except: 
        print('_convert_date_str failed with %y, try %Y') 
        df.columns = list(df.columns[:4]) + [datetime.strptime(d, "%m/%d/%Y").date().strftime("%Y-%m-%d") for d in df.columns[4:]] 
        
confirmed_global_df = pd.read_csv('time_series_covid19_confirmed_global.csv') 
_convert_date_str(confirmed_global_df) 
deaths_global_df = pd.read_csv('time_series_covid19_deaths_global.csv') 
_convert_date_str(deaths_global_df) 
recovered_global_df = pd.read_csv('time_series_covid19_recovered_global.csv') 
_convert_date_str(recovered_global_df)



In [4]:
deaths_global_df

Province/State      Country/Region        Lat        Long  2020-01-22  \
0              NaN         Afghanistan  33.939110   67.709953           0   
1              NaN             Albania  41.153300   20.168300           0   
2              NaN             Algeria  28.033900    1.659600           0   
3              NaN             Andorra  42.506300    1.521800           0   
4              NaN              Angola -11.202700   17.873900           0   
..             ...                 ...        ...         ...         ...   
275            NaN             Vietnam  14.058324  108.277199           0   
276            NaN  West Bank and Gaza  31.952200   35.233200           0   
277            NaN               Yemen  15.552727   48.516388           0   
278            NaN              Zambia -13.133897   27.849332           0   
279            NaN            Zimbabwe -19.015438   29.154857           0   

     2020-01-23  2020-01-24  2020-01-25  2020-01-26  2020-01-27  ...  \
0             0           0           0           0           0  ...   
1             0           0           0           0           0  ...   
2             0           0           0           0           0  ...   
3             0           0           0           0           0  ...   
4             0           0           0           0           0  ...   
..          ...         ...         ...         ...         ...  ...   
275           0           0           0           0           0  ...   
276           0           0           0           0           0  ...   
277           0           0           0           0           0  ...   
278           0           0           0           0           0  ...   
279           0           0           0           0           0  ...   

     2021-10-27  2021-10-28  2021-10-29  2021-10-30  2021-10-31  2021-11-01  \
0          7266        7268        7269        7272        7280        7281   
1          2893        2902        2909        2916        2924        2931   
2          5904        5907        5913        5918        5920        5924   
3           130         130         130         130         130         130   
4          1703        1705        1707        1708        1710        1713   
..          ...         ...         ...         ...         ...         ...   
275       21856       21910       21966       22030       22083       22131   
276        4651        4657        4663        4663        4663        4681   
277        1868        1874        1877        1880        1889        1890   
278        3660        3660        3660        3661        3661        3661   
279        4675        4675        4675        4675        4678        4679   

     2021-11-02  2021-11-03  2021-11-04  2021-11-05  
0          7281        7284        7284        7284  
1          2937        2940        2944        2948  
2          5927        5931        5936        5939  
3           130         130         130         130  
4          1713        1716        1718        1719  
..          ...         ...         ...         ...  
275       22205       22283       22342       22412  
276        4689        4694        4697        4705  
277        1894        1897        1901        1905  
278        3661        3661        3662        3662  
279        4683        4684        4685        4685  

[280 rows x 658 columns]

## 데이터 클랜징 작업

데이터 클랜징 작업 입니다. 아래 코드는 일부 음수가 있는 값들과 cruise ship의 감염자 수치가 잘못 들어간 것들을 정제한다.

In [5]:
import numpy as np 

removed_states = "Recovered|Grand Princess|Diamond Princess" 
removed_countries = "US|The West Bank and Gaza" 

confirmed_global_df.rename(columns={"Province/State": "Province_State", "Country/Region": "Country_Region"}, inplace=True)
deaths_global_df.rename(columns={"Province/State": "Province_State", "Country/Region": "Country_Region"}, inplace=True) 
recovered_global_df.rename(columns={"Province/State": "Province_State", "Country/Region": "Country_Region"}, inplace=True)

confirmed_global_df = confirmed_global_df[~confirmed_global_df["Province_State"].replace(np.nan, "nan").str.match(removed_states)]
deaths_global_df = deaths_global_df[~deaths_global_df["Province_State"].replace(np.nan, "nan").str.match(removed_states)] 
recovered_global_df = recovered_global_df[~recovered_global_df["Province_State"].replace(np.nan, "nan").str.match(removed_states)] 

confirmed_global_df = confirmed_global_df[~confirmed_global_df["Country_Region"].replace(np.nan, "nan").str.match(removed_countries)] 
deaths_global_df = deaths_global_df[~deaths_global_df["Country_Region"].replace(np.nan, "nan").str.match(removed_countries)]
recovered_global_df = recovered_global_df[~recovered_global_df["Country_Region"].replace(np.nan, "nan").str.match(removed_countries)]



confirmed_global_df, deaths_global_df, deaths_global_df 3개의 df를 각각 melt 함수를 사용하여<br>
confirmed_global_melt_df, deaths_global_melt_df, recovered_global_melt_df 각각 다른 df로 만들어준다.

In [6]:
confirmed_global_melt_df = confirmed_global_df.melt( 
    id_vars=['Country_Region', 'Province_State', 'Lat', 'Long'], value_vars=confirmed_global_df.columns[4:], var_name='Date', value_name='ConfirmedCases') 
deaths_global_melt_df = deaths_global_df.melt( 
    id_vars=['Country_Region', 'Province_State', 'Lat', 'Long'], value_vars=confirmed_global_df.columns[4:], var_name='Date', value_name='Deaths')
recovered_global_melt_df = deaths_global_df.melt( 
    id_vars=['Country_Region', 'Province_State', 'Lat', 'Long'], value_vars=confirmed_global_df.columns[4:], var_name='Date', value_name='Recovered')



confirmed_global_df를 기준으로 기존 279개의 entries가 181157로 늘어난 것을 확인 할 수 있습니다.

In [7]:
confirmed_global_df.info()
print()
confirmed_global_melt_df.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 277 entries, 0 to 279
Columns: 658 entries, Province_State to 2021-11-05
dtypes: float64(2), int64(654), object(2)
memory usage: 1.4+ MB

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 181158 entries, 0 to 181157
Data columns (total 6 columns):
 #   Column          Non-Null Count   Dtype  
---  ------          --------------   -----  
 0   Country_Region  181158 non-null  object 
 1   Province_State  55590 non-null   object 
 2   Lat             179850 non-null  float64
 3   Long            179850 non-null  float64
 4   Date            181158 non-null  object 
 5   ConfirmedCases  181158 non-null  int64  
dtypes: float64(2), int64(1), object(3)
memory usage: 8.3+ MB


train이라는 이름으로 confirmed_global_melt_df, deaths_global_melt_df, recovered_global_melt_df 각각으로 흩어져 있던 데이터를 하나로 합치는 과정을 진행 합니다.


In [8]:
train = confirmed_global_melt_df.merge(deaths_global_melt_df, on=['Country_Region', 'Province_State', 'Lat', 'Long', 'Date']) 
train = train.merge(recovered_global_melt_df, on=['Country_Region', 'Province_State', 'Lat', 'Long', 'Date'])
train



Country_Region Province_State        Lat        Long        Date  \
0              Afghanistan            NaN  33.939110   67.709953  2020-01-22   
1                  Albania            NaN  41.153300   20.168300  2020-01-22   
2                  Algeria            NaN  28.033900    1.659600  2020-01-22   
3                  Andorra            NaN  42.506300    1.521800  2020-01-22   
4                   Angola            NaN -11.202700   17.873900  2020-01-22   
...                    ...            ...        ...         ...         ...   
181153             Vietnam            NaN  14.058324  108.277199  2021-11-05   
181154  West Bank and Gaza            NaN  31.952200   35.233200  2021-11-05   
181155               Yemen            NaN  15.552727   48.516388  2021-11-05   
181156              Zambia            NaN -13.133897   27.849332  2021-11-05   
181157            Zimbabwe            NaN -19.015438   29.154857  2021-11-05   

        ConfirmedCases  Deaths  Recovered  
0                    0       0          0  
1                    0       0          0  
2                    0       0          0  
3                    0       0          0  
4                    0       0          0  
...                ...     ...        ...  
181153          953547   22412      22412  
181154          455099    4705       4705  
181155            9843    1905       1905  
181156          209852    3662       3662  
181157          133112    4685       4685  

[181158 rows x 8 columns]

# US데이터

날짜 컬럼명을 바꾸고, 필요없는 컬럼들을 drop해준다.

In [9]:
confirmed_us_df = pd.read_csv('time_series_covid19_confirmed_US.csv') 
deaths_us_df = pd.read_csv('time_series_covid19_deaths_US.csv')

confirmed_us_df.drop(['UID', 'iso2', 'iso3', 'code3', 'FIPS', 'Admin2', 'Combined_Key'], inplace=True, axis=1) 
deaths_us_df.drop(['UID', 'iso2', 'iso3', 'code3', 'FIPS', 'Admin2', 'Combined_Key', 'Population'], inplace=True, axis=1) 

confirmed_us_df.rename({'Long_': 'Long'}, axis=1, inplace=True) 
deaths_us_df.rename({'Long_': 'Long'}, axis=1, inplace=True)

_convert_date_str(confirmed_us_df) 
_convert_date_str(deaths_us_df)



데이터 클랜징 과정

In [10]:
confirmed_us_df = confirmed_us_df[~confirmed_us_df.Province_State.str.match("Diamond Princess|Grand Princess|Recovered|Northern Mariana Islands|American Samoa")] 
deaths_us_df = deaths_us_df[~deaths_us_df.Province_State.str.match("Diamond Princess|Grand Princess|Recovered|Northern Mariana Islands|American Samoa")]



일부 데이터 합치기

In [11]:
confirmed_us_df = confirmed_us_df.groupby(['Country_Region', 'Province_State']).sum().reset_index()
deaths_us_df = deaths_us_df.groupby(['Country_Region', 'Province_State']).sum().reset_index()



위도 경도 데이터 drop

In [12]:
confirmed_us_df.drop(['Lat', 'Long'], inplace=True, axis=1)
deaths_us_df.drop(['Lat', 'Long'], inplace=True, axis=1)



melt함수로 unpivot 해준다. <br>
train_us를 새롭게 생성한다.

In [13]:
confirmed_us_melt_df = confirmed_us_df.melt( 
    id_vars=['Country_Region', 'Province_State'], value_vars=confirmed_us_df.columns[2:], var_name='Date'
    , value_name='ConfirmedCases') 
deaths_us_melt_df = deaths_us_df.melt( 
    id_vars=['Country_Region', 'Province_State'], value_vars=deaths_us_df.columns[2:], var_name='Date'
    , value_name='Deaths')
train_us = confirmed_us_melt_df.merge(deaths_us_melt_df, on=['Country_Region', 'Province_State', 'Date'])


데이터 정리가 잘됌

In [14]:
train_us

Country_Region Province_State        Date  ConfirmedCases  Deaths
0                 US        Alabama  2020-01-22               0       0
1                 US         Alaska  2020-01-22               0       0
2                 US        Arizona  2020-01-22               0       0
3                 US       Arkansas  2020-01-22               0       0
4                 US     California  2020-01-22               0       0
...              ...            ...         ...             ...     ...
35311             US       Virginia  2021-11-05          933542   14125
35312             US     Washington  2021-11-05          737698    8798
35313             US  West Virginia  2021-11-05          276267    4518
35314             US      Wisconsin  2021-11-05          899647    9542
35315             US        Wyoming  2021-11-05          105318    1243

[35316 rows x 5 columns]

In [15]:
import pandas as pd

global 데이터 train과 train_us 데이터를 합친다.

In [16]:

train = pd.concat([train, train_us], axis=0, sort=False) 
train_us.rename({'Country_Region': 'country', 'Province_State': 'province', 'Date': 'date', 'ConfirmedCases': 'confirmed', 'Deaths': 'fatalities'}, axis=1, inplace=True)
train_us['country_province'] = train_us['country'].fillna('') + '/' + train_us['province'].fillna('')



In [17]:
train

Country_Region Province_State       Lat       Long        Date  \
0        Afghanistan            NaN  33.93911  67.709953  2020-01-22   
1            Albania            NaN  41.15330  20.168300  2020-01-22   
2            Algeria            NaN  28.03390   1.659600  2020-01-22   
3            Andorra            NaN  42.50630   1.521800  2020-01-22   
4             Angola            NaN -11.20270  17.873900  2020-01-22   
...              ...            ...       ...        ...         ...   
35311             US       Virginia       NaN        NaN  2021-11-05   
35312             US     Washington       NaN        NaN  2021-11-05   
35313             US  West Virginia       NaN        NaN  2021-11-05   
35314             US      Wisconsin       NaN        NaN  2021-11-05   
35315             US        Wyoming       NaN        NaN  2021-11-05   

       ConfirmedCases  Deaths  Recovered  
0                   0       0        0.0  
1                   0       0        0.0  
2                   0       0        0.0  
3                   0       0        0.0  
4                   0       0        0.0  
...               ...     ...        ...  
35311          933542   14125        NaN  
35312          737698    8798        NaN  
35313          276267    4518        NaN  
35314          899647    9542        NaN  
35315          105318    1243        NaN  

[216474 rows x 8 columns]

합쳐진 train 데이터 셋의 컬럼명을 일부 변경 하도록 하겠습니다. 그리고, country_privince 라는 컬럼을 추가 하여 <br>country와 province 값을 구분하여 넣는다



In [18]:
train.rename({'Country_Region': 'country', 'Province_State': 'province', 'Id': 'id', 'Date': 'date', 'ConfirmedCases': 'confirmed', 'Deaths': 'fatalities', 'Recovered': 'recovered'}, axis=1, inplace=True) 
train['country_province'] = train['country'].fillna('') + '/' + train['province'].fillna('')



In [19]:
train

country       province       Lat       Long        date  confirmed  \
0      Afghanistan            NaN  33.93911  67.709953  2020-01-22          0   
1          Albania            NaN  41.15330  20.168300  2020-01-22          0   
2          Algeria            NaN  28.03390   1.659600  2020-01-22          0   
3          Andorra            NaN  42.50630   1.521800  2020-01-22          0   
4           Angola            NaN -11.20270  17.873900  2020-01-22          0   
...            ...            ...       ...        ...         ...        ...   
35311           US       Virginia       NaN        NaN  2021-11-05     933542   
35312           US     Washington       NaN        NaN  2021-11-05     737698   
35313           US  West Virginia       NaN        NaN  2021-11-05     276267   
35314           US      Wisconsin       NaN        NaN  2021-11-05     899647   
35315           US        Wyoming       NaN        NaN  2021-11-05     105318   

       fatalities  recovered  country_province  
0               0        0.0      Afghanistan/  
1               0        0.0          Albania/  
2               0        0.0          Algeria/  
3               0        0.0          Andorra/  
4               0        0.0           Angola/  
...           ...        ...               ...  
35311       14125        NaN       US/Virginia  
35312        8798        NaN     US/Washington  
35313        4518        NaN  US/West Virginia  
35314        9542        NaN      US/Wisconsin  
35315        1243        NaN        US/Wyoming  

[216474 rows x 9 columns]

ww_df라는 데이터 프레임을 만들어서 그안에 전세계 데이터의 new_case와 growth factor 값을 날짜별로 구한다.

In [20]:
ww_df = train.groupby('date')[['confirmed', 'fatalities']].sum().reset_index() 
ww_df['new_case'] = ww_df['confirmed'] - ww_df['confirmed'].shift(1)
ww_df['growth_factor'] = ww_df['new_case'] / ww_df['new_case'].shift(1)
ww_df.tail()



date  confirmed  fatalities  new_case  growth_factor
649  2021-11-01  247144213     5006348  431651.0       1.408640
650  2021-11-02  247574422     5013603  430209.0       0.996659
651  2021-11-03  248091949     5021896  517527.0       1.202966
652  2021-11-04  248617813     5029528  525864.0       1.016109
653  2021-11-05  249133970     5038365  516157.0       0.981541

날짜별로 진단, 확진, 사망등의 통꼐를 내기 위해 아래와 같이 누적수치를 구한다.

In [21]:
ww_melt_df = pd.melt(ww_df, id_vars=['date'], value_vars=['confirmed', 'fatalities', 'new_case']) 
ww_melt_df



date   variable     value
0     2020-01-22  confirmed     557.0
1     2020-01-23  confirmed     655.0
2     2020-01-24  confirmed     941.0
3     2020-01-25  confirmed    1434.0
4     2020-01-26  confirmed    2118.0
...          ...        ...       ...
1957  2021-11-01   new_case  431651.0
1958  2021-11-02   new_case  430209.0
1959  2021-11-03   new_case  517527.0
1960  2021-11-04   new_case  525864.0
1961  2021-11-05   new_case  516157.0

[1962 rows x 3 columns]

# 데이터 시각화

데이터 시각화를 하기 위해 필요한 패키지를 import 한다.

In [22]:
from plotly import tools, subplots 
import plotly.offline as py 
py.init_notebook_mode(connected=True) 
import plotly.graph_objs as go 
import plotly.express as px 
import plotly.figure_factory as ff 
import plotly.io as pio
pio.templates.default = "plotly_dark" 
import matplotlib.pyplot as plt 




위에서 만들엇던 데이터셋 ww_melt_df를 이용해서 그래프를 그려보자.

In [23]:
fig = px.line(ww_melt_df, x="date", y="value", color='variable',
              title="Worldwide Confirmed/Death Cases Over Time") 
fig.show()



Log scale을 이용한 지표

In [24]:
fig = px.line(ww_melt_df, x="date", y="value", color="variable",
                title="Worldwid Confirmed/Death Cases Over Time (Log scale)",
             log_y=True)
fig.show()

사망률을 토대로 그래프를 그려보자.

In [25]:
ww_df['mortality'] = ww_df['fatalities'] / ww_df['confirmed'] 
fig = px.line(ww_df, x="date", y="mortality", title="Worldwide Mortality Rate Over Time")
fig.show()



초기에 사망률이 높아졌다가 점차적으로 안정을 찾는 모습을 확인 할 수 있다.

Growth Factor 그래프를 그려보자.

In [26]:
fig = px.line(ww_df, x="date", y="growth_factor", 
              title="Worldwide Growth Factor Over Time")
fig.add_trace(go.Scatter(x=[ww_df['date'].min(), ww_df['date'].max()], y=[1., 1.], name='Growth factor=1.', line=dict(dash='dash', color=('rgb(255, 0, 0)')))) 
fig.update_yaxes(range=[0., 5.])
fig.show()



# 국가별 코로나 분석


국가별로 코로나19의 추이가 어떻게 되는지를 확인해 보자.<br>
우선 국가별 사망자와 진단 데이터를 생성한다.

In [27]:
country_df = train.groupby(['date','country'])[['confirmed', 'fatalities']].sum().reset_index()
country_df.tail()

date             country  confirmed  fatalities
128179  2021-11-05             Vietnam     953547       22412
128180  2021-11-05  West Bank and Gaza     455099        4705
128181  2021-11-05               Yemen       9843        1905
128182  2021-11-05              Zambia     209852        3662
128183  2021-11-05            Zimbabwe     133112        4685

유니크한 국가명을 저장한다.

In [28]:
countries = country_df['country'].unique()
print(f'{len(countries)} countries are in dataset:\n{countries}')



196 countries are in dataset:
['Afghanistan' 'Albania' 'Algeria' 'Andorra' 'Angola'
 'Antigua and Barbuda' 'Argentina' 'Armenia' 'Australia' 'Austria'
 'Azerbaijan' 'Bahamas' 'Bahrain' 'Bangladesh' 'Barbados' 'Belarus'
 'Belgium' 'Belize' 'Benin' 'Bhutan' 'Bolivia' 'Bosnia and Herzegovina'
 'Botswana' 'Brazil' 'Brunei' 'Bulgaria' 'Burkina Faso' 'Burma' 'Burundi'
 'Cabo Verde' 'Cambodia' 'Cameroon' 'Canada' 'Central African Republic'
 'Chad' 'Chile' 'China' 'Colombia' 'Comoros' 'Congo (Brazzaville)'
 'Congo (Kinshasa)' 'Costa Rica' "Cote d'Ivoire" 'Croatia' 'Cuba' 'Cyprus'
 'Czechia' 'Denmark' 'Diamond Princess' 'Djibouti' 'Dominica'
 'Dominican Republic' 'Ecuador' 'Egypt' 'El Salvador' 'Equatorial Guinea'
 'Eritrea' 'Estonia' 'Eswatini' 'Ethiopia' 'Fiji' 'Finland' 'France'
 'Gabon' 'Gambia' 'Georgia' 'Germany' 'Ghana' 'Greece' 'Grenada'
 'Guatemala' 'Guinea' 'Guinea-Bissau' 'Guyana' 'Haiti' 'Holy See'
 'Honduras' 'Hungary' 'Iceland' 'India' 'Indonesia' 'Iran' 'Iraq'
 'Ireland' 'Israel'

196개의 국가가 있음을 확인할 수 있다.

In [29]:
len(countries)

196

각 국가들이 얼마나 많은 진단을 하고 있는지 확인해본다.<br>
confirmed 데이터를 활용한다.

In [30]:
target_date = country_df['date'].max() 



confirmed값이 1000 이상인 국가들을 가지고 탑 다운 차트를 그려보자.

In [31]:
top_country_df = country_df.query('(date == @target_date) & (confirmed > 1000)').sort_values('confirmed', ascending=False) 
top_country_melt_df = pd.melt(top_country_df, id_vars='country', value_vars=['confirmed', 'fatalities'])



In [32]:
fig = px.bar(top_country_melt_df.iloc[::-1],
             x='value', y='country', color='variable', barmode='group',
             title=f'Confirmed Cases/Deaths on {target_date}', 
             text='value', height=3000, orientation='h') 
fig.show()



TOp30 국가들의 진단 데이터를 차트로 그려보자.

In [33]:
top30_countries = top_country_df.sort_values('confirmed', ascending=False).iloc[:30]['country'].unique() 
top30_countries_df = country_df[country_df['country'].isin(top30_countries)] 
fig = px.line(top30_countries_df, x='date', y='confirmed', color='country', title=f'Confirmed Cases for top 30 country as of {target_date}') 
fig.show()



유럽과 남미 국가들이 많이보이는 경향이 있다.

사망자 데이터를 이용해서도 그려본다.

In [34]:
top30_countries = top_country_df.sort_values('confirmed', ascending=False).iloc[:30]['country'].unique() 
kor_countries_df = country_df[country_df['country']=='Korea, South'] 
fig = px.line(kor_countries_df, x='date', y='confirmed', color='country', title=f'Confirmed Cases for top 30 country as of {target_date}') 
fig.show()



사망률을 가지고 데이터 시각화를 진행하고 데이터를 새로 만들어준다.

In [35]:
top_country_df = country_df.query('(date == @target_date) & (confirmed > 100)')
top_country_df['mortality_rate'] = top_country_df['fatalities'] / top_country_df['confirmed']
top_country_df = top_country_df.sort_values('mortality_rate', ascending=False)



사망률이 적은 30위 나라의 지표

In [36]:
fig = px.bar(top_country_df[-30:], x='mortality_rate', y='country', title=f'Mortality rate LOW: top 30 countries on {target_date}', text='mortality_rate', height=800, orientation='h') 
fig.show()



한국이 사망률 적은 30위인 것을 알 수 있다.

총 순위

In [37]:
fig = px.bar(top_country_df, x='mortality_rate', y='country', title=f'Mortality rate LOW: top 30 countries on {target_date}', text='mortality_rate', height=800, orientation='h') 
fig.show()




사망률에서는 예메인 가장 높은 것을 보여준다.<br>
별개로 의료수준이나 대응력을 평가 할만한 수치이다.

In [38]:
fig = px.bar(top_country_df[-30:], x='mortality_rate', y='country', title=f'Mortality rate LOW: top 30 countries on {target_date}', text='mortality_rate', height=800, orientation='h') 
fig.show()



세계지도위에 시각화를 해보자.<br>
진단과 사망률을 가지고 세가지 차트를 만들어 본다.

In [39]:
all_country_df = country_df.query('date == @target_date')
all_country_df['confirmed_log1p'] = np.log10(all_country_df['confirmed'] + 1) 
all_country_df['fatalities_log1p'] = np.log10(all_country_df['fatalities'] + 1) 
all_country_df['mortality_rate'] = all_country_df['fatalities'] / all_country_df['confirmed']



진단수 시각화

In [40]:
fig = px.choropleth(all_country_df, locations="country",
                    locationmode='country names', color="confirmed_log1p",
                    hover_name="country", hover_data=["confirmed", 'fatalities', 'mortality_rate'],
                    range_color=[all_country_df['confirmed_log1p'].min(), all_country_df['confirmed_log1p'].max()], 
                    color_continuous_scale="peach",
                    title='Countries with Confirmed Cases') 
# I'd like to update colorbar to show raw values, but this does not work somehow... # Please let me know if you know how to do this!!
trace1 = list(fig.select_traces())[0]
trace1.colorbar = go.choropleth.ColorBar(
    tickvals=[0, 1, 2, 3, 4, 5, 6, 7, 8], 
    ticktext=['1', '10', '100', '1000','10000', '100000', '1000000', '10000000', '100000000'])
fig.show()



사망률 데이터 시각화

In [41]:
fig = px.choropleth(all_country_df,
                    locations="country", locationmode='country names', color="mortality_rate",
                    hover_name="country", range_color=[0, 0.10], 
                    color_continuous_scale="peach", title='Countries with mortality rate') 
fig.show()



# 최초로 10명이 사망한 이후 추이


In [42]:
n_countries = 20
n_start_death = 10 
fatality_top_countires = top_country_df.sort_values('fatalities', ascending=False).iloc[:n_countries]['country'].values
country_df['date'] = pd.to_datetime(country_df['date']) 
df_list = [] 
for country in fatality_top_countires: 
    this_country_df = country_df.query('country == @country') 
    start_date = this_country_df.query('fatalities > @n_start_death')['date'].min() 
    this_country_df = this_country_df.query('date >= @start_date') 
    this_country_df['date_since'] = this_country_df['date'] - start_date 
    this_country_df['fatalities_log1p'] = np.log10(this_country_df['fatalities'] + 1) 
    this_country_df['fatalities_log1p'] -= this_country_df['fatalities_log1p'].values[0] 
    df_list.append(this_country_df)
tmpdf = pd.concat(df_list) 
tmpdf['date_since_days'] = tmpdf['date_since'] / pd.Timedelta('1 days')
fig = px.line(tmpdf,
              x='date_since_days', y='fatalities_log1p', color='country', 
              title=f'Fatalities by country since 10 deaths, as of {target_date}') 
fig.add_trace(go.Scatter(x=[0, 28], y=[0, 4], name='Double by 7 days', line=dict(dash='dash', color=('rgb(200, 200, 200)'))))
fig.add_trace(go.Scatter(x=[0, 56], y=[0, 4], name='Double by 14 days', line=dict(dash='dash', color=('rgb(200, 200, 200)')))) 
fig.add_trace(go.Scatter(x=[0, 84], y=[0, 4], name='Double by 21 days', line=dict(dash='dash', color=('rgb(200, 200, 200)')))) 
fig.show()



# 국가 별 일일 신규 확인 사례

국가 별 일일 신규 확진자 사례를 시각화 하도록 한다.

In [43]:
country_df['prev_confirmed'] = country_df.groupby('country')['confirmed'].shift(1) 
country_df['new_case'] = country_df['confirmed'] - country_df['prev_confirmed'] 
country_df['new_case'].fillna(0, inplace=True) 
top30_country_df = country_df[country_df['country'].isin(top30_countries)]

fig = px.line(top30_country_df,
              x='date', y='new_case', color='country', 
              title=f'DAILY NEW Confirmed cases by country') 
fig.show()



일일 확진자가 어떻게 나오는지 알 수 있고 <br>
범례를 클릭하면 해당 국가것만 볼 수 있다.

한국 일일 확진자수

In [44]:
country_df['prev_confirmed'] = country_df.groupby('country')['confirmed'].shift(1) 
country_df['new_case'] = country_df['confirmed'] - country_df['prev_confirmed'] 
country_df['new_case'].fillna(0, inplace=True) 
kor_country_df = country_df[country_df['country']=='Korea, South']

fig = px.line(kor_country_df,
              x='date', y='new_case', color='country', 
              title=f'DAILY NEW Confirmed cases by country') 
fig.show()





# 국가별 신규 확진자 factor 지표


In [45]:
country_df['avg_new_case'] = country_df.groupby('country')['new_case'].rolling(7).mean().reset_index(0, drop=True)
country_df['prev_new_case'] = country_df.groupby('country')['avg_new_case'].shift(1) 
country_df['growth_factor'] = country_df['avg_new_case'] / country_df['prev_new_case']

country_df['growth_factor'].fillna(0, inplace=True)
top30_country_df = country_df[country_df['country'].isin(top30_countries)] 

fig = px.line(top30_country_df,
              x='date', y='growth_factor', color='country', 
              title=f'Growth factor by country') 

fig.add_trace(go.Scatter(x=[ww_df['date'].min(), ww_df['date'].max()], y=[1., 1.], name='Growth factor=1.', 
                         line=dict(dash='dash', color=('rgb(255, 0, 0)'))))
fig.update_yaxes(range=[0., 5.]) 
fig.show()



한국

In [46]:
country_df['avg_new_case'] = country_df.groupby('country')['new_case'].rolling(7).mean().reset_index(0, drop=True)
country_df['prev_new_case'] = country_df.groupby('country')['avg_new_case'].shift(1) 
country_df['growth_factor'] = country_df['avg_new_case'] / country_df['prev_new_case']

country_df['growth_factor'].fillna(0, inplace=True)
kor_country_df = country_df[country_df['country']=='Korea, South'] 

fig = px.line(kor_country_df,
              x='date', y='growth_factor', color='country', 
              title=f'Growth factor by country') 

fig.add_trace(go.Scatter(x=[ww_df['date'].min(), ww_df['date'].max()], y=[1., 1.], name='Growth factor=1.', 
                         line=dict(dash='dash', color=('rgb(255, 0, 0)'))))
fig.update_yaxes(range=[0., 5.]) 
fig.show()


